In [8]:
import random
import re
import collections

class HangmanGame:
    def __init__(self, full_dictionary_location='words_train_split.txt'):

        self.guessed_letters = []

        self.full_dictionary = self.build_dictionary(full_dictionary_location)

        val_dictionary_path = 'words_val_split.txt'
        self.val_dictionary = self.build_dictionary(val_dictionary_path)
            
        

        self.full_dictionary_common_letter_sorted = collections.Counter("".join(self.full_dictionary)).most_common()
        
        self.current_dictionary = []        

    def guess(self, word): # word input example: "_ p p _ e "

        letters_by_frequency = ['e', 't', 'a', 'o', 'i', 'n', 's', 'h', 'r', 'd', 'l', 'c', 'u', 'm', 'w', 'f', 'g', 'y', 'p', 'b', 'v', 'k', 'j', 'x', 'q', 'z']

        ###############################################
        # Replace with your own "guess" function here #
        ###############################################

        # clean the word so that we strip away the space characters
        # replace "_" with "." as "." indicates any character in regular expressions
        clean_word = word[::2].replace("_",".")
        
        # find length of passed word
        len_word = len(clean_word)
        
        # grab current dictionary of possible words from self object, initialize new possible words dictionary to empty
        current_dictionary = self.current_dictionary
        new_dictionary = []
        
        # iterate through all of the words in the old plausible dictionary
        for dict_word in current_dictionary:
            # continue if the word is not of the appropriate length
            if len(dict_word) != len_word:
                continue
                
            # if dictionary word is a possible match then add it to the current dictionary
            if re.match(clean_word,dict_word):
                new_dictionary.append(dict_word)
        
        # overwrite old possible words dictionary with updated version
        self.current_dictionary = new_dictionary
        
        
        # count occurrence of all characters in possible word matches
        full_dict_string = "".join(new_dictionary)
        
        c = collections.Counter(full_dict_string)
        sorted_letter_count = c.most_common()                   
        
        guess_letter = '!'
        
        # return most frequently occurring letter in all possible words that hasn't been guessed yet
        for letter,instance_count in sorted_letter_count:
            if letter not in self.guessed_letters:
                guess_letter = letter
                break
            
        # if no word matches in training dictionary, default back to ordering of full dictionary
        if guess_letter == '!':
            sorted_letter_count = self.full_dictionary_common_letter_sorted
            for letter,instance_count in sorted_letter_count:
                if letter not in self.guessed_letters:
                    guess_letter = letter
                    break            
        
        return guess_letter
    
    def build_dictionary(self, dictionary_file_location):
        text_file = open(dictionary_file_location,"r")
        full_dictionary = text_file.read().splitlines()
        text_file.close()
        return full_dictionary
        
    def start_game(self, secret_word=None, verbose=True):
        self.guessed_letters = []
        self.current_dictionary = self.full_dictionary
        if secret_word is None:
            secret_word = random.choice(self.val_dictionary)
        word = ' '.join(['_' for _ in secret_word])
        tries_remains = 6
        if verbose:
            print("Successfully start a new game! # of tries remaining: {0}. Word: {1}.".format(tries_remains, word))
        while tries_remains > 0:
            # get guessed letter from user code
            guess_letter = self.guess(word)
            
            # append guessed letter to guessed letters field in hangman object
            self.guessed_letters.append(guess_letter)
            if verbose:
                print("Guessing letter: {0}".format(guess_letter))

            if guess_letter in secret_word:
                # update word with guessed letter
                word = ' '.join([letter if letter == guess_letter else word[index*2] for index, letter in enumerate(secret_word)])
            if guess_letter not in secret_word:
                tries_remains -= 1

            if tries_remains > 0:
                status = 'ongoing'
            if '_' not in word:
                status = 'success'            
            if tries_remains == 0:
                status = 'failed'
            res = {'status': status, 'tries_remains': tries_remains, 'word': word}
            print(res)

            if status == 'success':
                print("Successfully finished game, the word was: {0}!".format(secret_word))
                return True

            if status == 'failed':
                print("Failed game because of: # of tries exceeded!")
                return False
            
        return status=="success"

In [9]:
num_success = 0

words = open('words_val_split.txt', 'r').read().splitlines()

for word in words[:5000]:
    game = HangmanGame()
    num_success += int(game.start_game(secret_word=word, verbose=False))

print("Success rate: {0}".format(num_success/len(words)))

{'status': 'ongoing', 'tries_remains': 5, 'word': '_ _ _ _ _ _ _ _ _'}
{'status': 'ongoing', 'tries_remains': 5, 'word': 'i _ _ _ _ _ _ _ _'}
{'status': 'ongoing', 'tries_remains': 5, 'word': 'i _ _ n _ _ _ _ _'}
{'status': 'ongoing', 'tries_remains': 5, 'word': 'i _ o n _ _ _ _ _'}
{'status': 'ongoing', 'tries_remains': 5, 'word': 'i r o n _ _ r _ _'}
{'status': 'ongoing', 'tries_remains': 4, 'word': 'i r o n _ _ r _ _'}
{'status': 'ongoing', 'tries_remains': 4, 'word': 'i r o n _ _ r _ s'}
{'status': 'ongoing', 'tries_remains': 4, 'word': 'i r o n _ _ r k s'}
{'status': 'ongoing', 'tries_remains': 4, 'word': 'i r o n _ a r k s'}
{'status': 'ongoing', 'tries_remains': 3, 'word': 'i r o n _ a r k s'}
{'status': 'ongoing', 'tries_remains': 2, 'word': 'i r o n _ a r k s'}
{'status': 'ongoing', 'tries_remains': 1, 'word': 'i r o n _ a r k s'}
{'status': 'failed', 'tries_remains': 0, 'word': 'i r o n _ a r k s'}
Failed game because of: # of tries exceeded!
{'status': 'ongoing', 'tries_rema

In [10]:
words.index(word)

4999

In [12]:
num_success / 5000

0.1798